# API URL Health Checker Generator

This notebook demonstrates an OpenAI API integration project that automatically generates a Python CLI tool for URL health monitoring. 

## Features:
- **Smart Configuration Management**: Environment variable handling with validation
- **AI-Powered Code Generation**: Uses OpenAI API to generate complete Python scripts
- **URL Health Monitoring**: Generated tool checks website availability and response times
- **CLI Interface**: Command-line tool with customizable parameters
- **Comprehensive Reporting**: CSV output and summary statistics
- **Error Handling**: Robust timeout and retry mechanisms

## Generated Tool Capabilities:
- Batch URL testing from file input
- Response time measurement
- Status code reporting  
- Configurable timeouts and retries
- CSV export functionality
- Summary statistics display

This project showcases how to leverage AI APIs for automated code generation and practical DevOps tooling.

In [12]:
# Install required packages
!pip install openai python-dotenv

In [5]:
# Configuration Class
import os, re, sys, pathlib
from dotenv import load_dotenv
from openai import OpenAI

class Config:
    def __init__(self):
        load_dotenv()
        
    def require_env(self, name: str) -> str:
        val = os.getenv(name)
        if not val:
            print(f"[!] Missing environment variable: {name}", file=sys.stderr)
            sys.exit(1)
        return val
    
    @property
    def api_key(self) -> str:
        # Get API key from environment variable
        key = self.require_env('OPENAI_API_KEY')
        if not key.startswith('sk-'):
            key = f"sk-{key}"
        return key
    
    @property
    def base_url(self) -> str:
        return self.require_env('BASE_URL')
    
    @property
    def model_name(self) -> str:
        return self.require_env('MODEL_NAME')

# Test the configuration
config = Config()
print("Configuration loaded successfully!")
# Uncomment below to test (but don't commit these with actual values visible)
# print(f"API Key: {config.api_key[:15]}...")
# print(f"Base URL: {config.base_url}")
# print(f"Model: {config.model_name}")

Configuration loaded successfully!


In [8]:
# prompt for URL health checker
SYSTEM_PROMPT = """You are a Python developer. Create a simple URL health checker CLI.
Return ONLY ONE Python script that:
1. Reads URLs from a text file (one per line)
2. Pings each URL with GET requests
3. Handles timeouts and retries
4. Writes results to CSV (url, status_code, response_time_ms, success)
5. Prints a summary table

Use requests library and basic error handling. Keep it simple and functional."""

USER_PROMPT = """Create a Python CLI script called url_checker.py that:

1. Takes command line arguments:
   - --input: input file with URLs (default: urls.txt)
   - --output: output CSV file (default: results.csv)
   - --timeout: request timeout in seconds (default: 5)
   - --retries: number of retries (default: 3)

2. Reads URLs from input file (ignore empty lines and comments starting with #)

3. For each URL:
   - Make GET request with timeout
   - Retry on failure up to specified retries
   - Record: URL, status code, response time in ms, success (True/False)

4. Write results to CSV file

5. Print summary:
   - Total URLs checked
   - Successful requests
   - Failed requests
   - Average response time

Keep the code simple, well-commented, and easy to understand."""

def generate_url_checker():
    cfg = Config()
    client = OpenAI(api_key=cfg.api_key, base_url=cfg.base_url)

    resp = client.chat.completions.create(
        model=cfg.model_name,
        messages=[
            {"role": "system", "content": SYSTEM_PROMPT},
            {"role": "user", "content": USER_PROMPT},
        ],
        temperature=0.2,
        max_tokens=200000,
    )

    return resp.choices[0].message.content

# Generate and display the URL checker script
print("Generating URL checker CLI script...")
script_content = generate_url_checker()
print("\n" + "="*60)
print("GENERATED URL CHECKER SCRIPT:")
print("="*60)
print(script_content)

Generating URL checker CLI script...

GENERATED URL CHECKER SCRIPT:
Okay, I need to create a Python CLI script called url_checker.py based on the user's requirements. Let me start by breaking down the requirements step by step.

First, the script must accept command-line arguments: --input, --output, --timeout, and --retries. I'll use the argparse module for that. The defaults are urls.txt, results.csv, 5 seconds, and 3 retries respectively. So I'll set those up as the default values in the argparse arguments.

Next, the script should read URLs from the input file. I need to open the file, read each line, and ignore empty lines and those starting with a #. So I'll loop through each line, strip whitespace, check if the line is not empty and doesn't start with a comment character.

Then, for each URL, I have to make a GET request with the specified timeout and retry on failure. The requests library will handle the GET requests. But I need to handle exceptions like ConnectionError, Timeou

In [9]:
# Save the generated script to a file
script_content = generate_url_checker()

# Extract just the Python code if it's wrapped in markdown code blocks
import re
code_match = re.search(r'```python\n(.*?)\n```', script_content, re.DOTALL)
if code_match:
    clean_script = code_match.group(1)
else:
    clean_script = script_content

# Save to file
with open('url_checker.py', 'w') as f:
    f.write(clean_script)

print("\nTo use the script:")
print("1. Create a urls.txt file with URLs (one per line)")
print("2. Run: python url_checker.py --input urls.txt --output results.csv")
print("\nExample urls.txt content:")
print("https://www.google.com")
print("https://www.github.com")
print("https://httpbin.org/status/200")
print("https://httpbin.org/delay/2")


To use the script:
1. Create a urls.txt file with URLs (one per line)
2. Run: python url_checker.py --input urls.txt --output results.csv

Example urls.txt content:
https://www.google.com
https://www.github.com
https://httpbin.org/status/200
https://httpbin.org/delay/2
